In [1]:
import requests
import pandas as pd
import numpy as np

http_proxy  = "http://proxy-web.micron.com:80"
https_proxy = "http://proxy-web.micron.com:80"
proxyDict = { 
    "http":http_proxy, 
    "https":https_proxy              
}

pd.set_option('display.max_rows', None) #show every row for pandas
pd.set_option('display.max_columns', None) #show every column for pandas

In [2]:
# sii:上市, otc:上櫃
# TWSE之數據是至該季的累計數據而非單季數據, EX: Q3=> TWSE: Q1~Q3, 財報狗:Q3
def financial_statement(year, season, stocktype, type='綜合損益彙總表'):
    if year >= 1000:
        year -= 1911
        
    if type == '綜合損益彙總表':
        url = 'http://mops.twse.com.tw/mops/web/ajax_t163sb04'
    elif type == '資產負債彙總表':
        url = 'http://mops.twse.com.tw/mops/web/ajax_t163sb05'
    elif type == '營益分析彙總表':
        url = 'http://mops.twse.com.tw/mops/web/ajax_t163sb06'
    else:
        print('type does not match')
    
    r = requests.post(url, {
        'encodeURIComponent':1,
        'step':1,
        'firstin':1,
        'off':1,
        'TYPEK':stocktype,
        'year':str(year),
        'season':str(season),
    }, stream=True, verify=False, proxies=proxyDict)
    
    r.encoding = 'utf8'
    dfs = pd.read_html(r.text)
    
    
    for i, df in enumerate(dfs):
        df.columns = df.iloc[0]
        dfs[i] = df.iloc[1:]
        
    df = pd.concat(dfs).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df['公司代號'] != '公司代號']
    df = df[~df['公司代號'].isnull()]
    
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_suffix.html
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_prefix.html
    suffix_format = "_{0}Q{1}".format(year, season)
    
    #return df.add_suffix(suffix_format)
    return df

In [3]:
def generate_df_for_stocktype(year, season, howmany_year_data, stocktype, title_name, with_col_name, sheettype):
    df = financial_statement(year, season, stocktype, type=sheettype)[['公司代號','公司名稱',with_col_name]]
    df.rename(columns = {df.columns[2]: '{0}_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

    for i in range(howmany_year_data*4):
        # calculate previous quarter data 107Q1 => we want the previous data is 106Q4 AND then 106Q3, 106Q2, 106Q1, 105Q4
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        #https://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.merge.html
        dfanother = financial_statement(year, season, stocktype, type=sheettype)[['公司代號',with_col_name]]    
        print(dfanother.columns[1])

        dfanother.rename(columns = {dfanother.columns[1]: '{0}_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

        df = df.merge(dfanother, on='公司代號', how='inner')
        print("year:", year)
        #print("year: {0}".format(year))
        print("season:", season)
        #print("season: {0}".format(season))

    return df

In [4]:
df_gross_profit_sii = generate_df_for_stocktype(107, 1, 3, 'sii', 'GrossProfit', '營業毛利（毛損）', '綜合損益彙總表')

df_gross_profit_sii

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



營業毛利（毛損）
year: 106
season: 4
營業毛利（毛損）
year: 106
season: 3
營業毛利（毛損）
year: 106
season: 2
營業毛利（毛損）
year: 106
season: 1
營業毛利（毛損）
year: 105
season: 4
營業毛利（毛損）
year: 105
season: 3
營業毛利（毛損）
year: 105
season: 2
營業毛利（毛損）
year: 105
season: 1
營業毛利（毛損）
year: 104
season: 4
營業毛利（毛損）
year: 104
season: 3
營業毛利（毛損）
year: 104
season: 2
營業毛利（毛損）
year: 104
season: 1


公司代號     公司名稱 GrossProfit_107Q1 GrossProfit_106Q4 GrossProfit_106Q3  \
0    2801     彰化銀行               NaN               NaN               NaN   
1    2809     京城銀行               NaN               NaN               NaN   
2    2812     台中銀行               NaN               NaN               NaN   
3    2820       華票               NaN               NaN               NaN   
4    2834     臺灣企銀               NaN               NaN               NaN   
5    2836       高銀               NaN               NaN               NaN   
6    2838     聯邦銀行               NaN               NaN               NaN   
7    2845     遠東商銀               NaN               NaN               NaN   
8    2849     安泰銀行               NaN               NaN               NaN   
9    2855     統一證券               NaN               NaN               NaN   
10   2856     元富證券               NaN               NaN               NaN   
11   6005      群益證               NaN               NaN               NaN   
12   6024      群益期               NaN               NaN               NaN   
13   1101       台泥           5790640          18912914          12524003   
14   1102       亞泥           3329473          10171018           5961663   
15   1103       嘉泥             54830            282321            236084   
16   1104     環球水泥            138524            537908            423796   
17   1108     幸福水泥             20566            128501            205206   
18   1109     信大水泥            241008           1256014            722987   
19   1110       東泥             34457            -43205            -40823   
20   1201     味全公司           1104857           5553412           3978680   
21   1203     味王公司            488478           2020256           1499643   
22   1210     大成長城           2552191          10232733           7556152   
23   1213       大飲             16020             68492             62387   
24   1215     卜蜂企業            732606           3327986           2434799   
25   1216       統一          35429055         132740671         102775385   
26   1217      愛之味            325598           1304671           1074001   
27   1218     泰山企業            305219           1331364           1053629   
28   1219     福壽實業            268613            896460            635738   
29   1220       台榮             65957            274884            209987   
30   1225      福懋油            251047           1035870            790079   
31   1227       佳格           2289204           7399955           5484014   
32   1229     聯華實業            203445           1025092            777271   
33   1231     聯華食品            459088           1445489           1088640   
34   1232      大統益            429340           1685216           1249807   
35   1233       天仁            321597           1212380            912129   
36   1234       黑松            474380           2335035           1842255   
37   1235       興泰              -621              4798             17469   
38   1236     宏亞食品            161160            502744            303102   
39   1256  鮮活果汁-KY            221370            872790            734664   
40   1262    綠悅-KY             98650           1394442           1192669   
41   1301       台塑           9349215          33469176          25012107   
42   1303     南亞塑膠          13756954          49934342          36977513   
43   1304       台聚           1845606           7126932           5307297   
44   1305       華夏            970114           2776931           2025996   
45   1307     三芳化工            553730           2903725           2373599   
46   1308       亞聚             77798            697076            543453   
47   1309     台達化工            375252           1433704            949060   
48   1310       台苯            546139           1689216           1334821   
49   1312     國喬石化           1124826           3793985           2693426   
50   1313       聯成           1019444           3860351           2761819   
51   1314      中石化           1257893           537101

In [5]:
df_gross_profit_otc = generate_df_for_stocktype(107, 1, 3, 'otc', 'GrossProfit', '營業毛利（毛損）', '綜合損益彙總表')

df_gross_profit_otc

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



營業毛利（毛損）
year: 106
season: 4
營業毛利（毛損）
year: 106
season: 3
營業毛利（毛損）
year: 106
season: 2
營業毛利（毛損）
year: 106
season: 1
營業毛利（毛損）
year: 105
season: 4
營業毛利（毛損）
year: 105
season: 3
營業毛利（毛損）
year: 105
season: 2
營業毛利（毛損）
year: 105
season: 1
營業毛利（毛損）
year: 104
season: 4
營業毛利（毛損）
year: 104
season: 3
營業毛利（毛損）
year: 104
season: 2
營業毛利（毛損）
year: 104
season: 1


公司代號    公司名稱 GrossProfit_107Q1 GrossProfit_106Q4 GrossProfit_106Q3  \
0    6015    宏遠證券               NaN               NaN               NaN   
1    6016    康和證券               NaN               NaN               NaN   
2    6020     大展證               NaN               NaN               NaN   
3    6021     大慶證               NaN               NaN               NaN   
4    6023    元大期貨               NaN               NaN               NaN   
5    6026    福邦證券               NaN               NaN               NaN   
6    1258   其祥-KY            111964            438375            363917   
7    1259      安心            300863           1276789            973431   
8    1264      德麥            356578           1385575           1009112   
9    1333     恩得利             10606             50907             46654   
10   1336      台翰             90384            386849            281625   
11   1565    精華光學            580094           2544591           1906146   
12   1566      捷邦            158604            762675            568498   
13   1569      濱川            141677            810337            547434   
14   1570    力肯實業             30939            189520            152130   
15   1580    新麥企業            345430           1897745           1360049   
16   1584    精剛精密              5585             28645             27183   
17   1586    和勤精機             99280            456121            322757   
18   1591   駿吉-KY             11650             70370             47265   
19   1593      祺驊             40796            261398            188936   
20   1595    川寶科技            118570            432536            314232   
21   1597      直得            241486            622967            419662   
22   1599     宏佳騰             62450            592466            402915   
23   1742      台蠟              4553             44916             36431   
24   1752      南光            132171            516345            361955   
25   1777      生泰             63015            199828            156851   
26   1781    合世生醫              4721             53074             44628   
27   1784    訊聯生技            109602            366203            262143   
28   1785     光洋科            475117           1649445           1082746   
29   1787     福盈科            150144            595719            443747   
30   1788    杏昌生技            168364            668577            488778   
31   1795    美時製藥            683280           3079674           2203513   
32   1799      易威              9097             36446             24975   
33   1813     寶利徠             15826             82193             67938   
34   1815    富喬工業            322084           1309981           1142416   
35   2035    唐榮公司            -73079            540270            483412   
36   2061      風青             15368             75209             55061   
37   2063      世鎧             77992            278448            208590   
38   2064      晉椿             64842            227669            165388   
39   2066      世德             73205            383881            285341   
40   2067      嘉鋼             54169            194613            126202   
41   2221    大甲永和             65253            230026            158174   
42   2230      泰茂             16171            103826             72899   
43   2233      宇隆            268628            957212            721762   
44   2235      謚源             44231            237777            195903   
45   2596    綠意開發            264675            485117            311417   
46   2640     大車隊            217382            786943            592469   
47   2641    正德海運             39129             96100             87773   
48   2718      晶悅              4698             19167              8713   
49   2719     燦星旅             57678            318666            241735   
50   2724   富驛-KY            -11261            112005             67692   
51   2726   雅茗-KY            278174           1088792            808511   
52   2729    瓦城泰統            5

In [6]:
#Database-style DataFrame joining/merging: join, merge
#Concatenating objects: concat, append

#ignore_index = True 可以忽略合併時舊的 index 欄位，改採用自動產生的 index
df_gross_profit = pd.concat([df_gross_profit_sii,df_gross_profit_otc],axis=0, ignore_index=True)

df_gross_profit

公司代號     公司名稱 GrossProfit_107Q1 GrossProfit_106Q4 GrossProfit_106Q3  \
0     2801     彰化銀行               NaN               NaN               NaN   
1     2809     京城銀行               NaN               NaN               NaN   
2     2812     台中銀行               NaN               NaN               NaN   
3     2820       華票               NaN               NaN               NaN   
4     2834     臺灣企銀               NaN               NaN               NaN   
5     2836       高銀               NaN               NaN               NaN   
6     2838     聯邦銀行               NaN               NaN               NaN   
7     2845     遠東商銀               NaN               NaN               NaN   
8     2849     安泰銀行               NaN               NaN               NaN   
9     2855     統一證券               NaN               NaN               NaN   
10    2856     元富證券               NaN               NaN               NaN   
11    6005      群益證               NaN               NaN               NaN   
12    6024      群益期               NaN               NaN               NaN   
13    1101       台泥           5790640          18912914          12524003   
14    1102       亞泥           3329473          10171018           5961663   
15    1103       嘉泥             54830            282321            236084   
16    1104     環球水泥            138524            537908            423796   
17    1108     幸福水泥             20566            128501            205206   
18    1109     信大水泥            241008           1256014            722987   
19    1110       東泥             34457            -43205            -40823   
20    1201     味全公司           1104857           5553412           3978680   
21    1203     味王公司            488478           2020256           1499643   
22    1210     大成長城           2552191          10232733           7556152   
23    1213       大飲             16020             68492             62387   
24    1215     卜蜂企業            732606           3327986           2434799   
25    1216       統一          35429055         132740671         102775385   
26    1217      愛之味            325598           1304671           1074001   
27    1218     泰山企業            305219           1331364           1053629   
28    1219     福壽實業            268613            896460            635738   
29    1220       台榮             65957            274884            209987   
30    1225      福懋油            251047           1035870            790079   
31    1227       佳格           2289204           7399955           5484014   
32    1229     聯華實業            203445           1025092            777271   
33    1231     聯華食品            459088           1445489           1088640   
34    1232      大統益            429340           1685216           1249807   
35    1233       天仁            321597           1212380            912129   
36    1234       黑松            474380           2335035           1842255   
37    1235       興泰              -621              4798             17469   
38    1236     宏亞食品            161160            502744            303102   
39    1256  鮮活果汁-KY            221370            872790            734664   
40    1262    綠悅-KY             98650           1394442           1192669   
41    1301       台塑           9349215          33469176          25012107   
42    1303     南亞塑膠          13756954          49934342          36977513   
43    1304       台聚           1845606           7126932           5307297   
44    1305       華夏            970114           2776931           2025996   
45    1307     三芳化工            553730           2903725           2373599   
46    1308       亞聚             77798            697076            543453   
47    1309     台達化工            375252           1433704            949060   
48    1310       台苯            546139           1689216           1334821   
49    1312     國喬石化           1124826           3793985           2693426   
50    1313       聯成           1019444           3860351           2761819   
51

In [7]:
#檢查column資料型態

#df_eps.info() #non-null object
#df_eps.dtypes #object
#df_eps.applymap(np.isreal) #all False
'''
公司代號              int64
公司名稱             object
GrossProfit_107Q1    float64
GrossProfit_106Q4    float64
GrossProfit_106Q3    float64
GrossProfit_106Q2    float64
GrossProfit_106Q1    float64
GrossProfit_105Q4    float64
GrossProfit_105Q3    float64
GrossProfit_105Q2    float64
GrossProfit_105Q1    float64
GrossProfit_104Q4    float64
GrossProfit_104Q3    float64
GrossProfit_104Q2    float64
GrossProfit_104Q1    float64
dtype: object
'''

df_gross_profit = df_gross_profit.convert_objects(convert_numeric=True) #轉成float型態方便後續處理

df_gross_profit.convert_objects(convert_numeric=True).dtypes #轉成float型態方便後續處理

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:25: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:27: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.


公司代號                   int64
公司名稱                  object
GrossProfit_107Q1    float64
GrossProfit_106Q4    float64
GrossProfit_106Q3    float64
GrossProfit_106Q2    float64
GrossProfit_106Q1    float64
GrossProfit_105Q4    float64
GrossProfit_105Q3    float64
GrossProfit_105Q2    float64
GrossProfit_105Q1    float64
GrossProfit_104Q4    float64
GrossProfit_104Q3    float64
GrossProfit_104Q2    float64
GrossProfit_104Q1    float64
dtype: object

In [8]:
def isFloat(element):  
    try:
        float(element)
        return True
    except ValueError:
        return False

In [9]:
def growth_func(row, year, season):
    previous_year = year - 1
    #判斷是否為文字而非數字
    if(isFloat(row['GrossProfit_{0}Q{1}'.format(year, season)]) == True):
        subsequent_value = float(row['GrossProfit_{0}Q{1}'.format(year, season)])
        previous_value = float(row['GrossProfit_{0}Q{1}'.format(previous_year, season)])
   
        if(previous_value == 0):
            result = ((subsequent_value - previous_value)/np.abs(subsequent_value))*100
        else:
            result = ((subsequent_value - previous_value)/np.abs(previous_value))*100            
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
     
    else:
        return 'NoValue'

In [10]:
def ma2q_growth_func(row, year, season):
    #判斷是否為文字而非數字
    if(isFloat(row['GrossProfit_{0}Q{1}'.format(year, season)])):
        previous_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        subsequent_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        
        result = ((subsequent_value + previous_value)/2)
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
    
    else:
        return 'NoValue'

In [11]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = 107
season = 1
howmany_year_data = 3

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4)):
    df_gross_profit['Growth_{0}Q{1}'.format(year, season)] = df_gross_profit.apply (lambda row: growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [12]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = 107
season = 1
howmany_year_data = 3

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4-1)):
    df_gross_profit['2QMAGrowth_{0}Q{1}'.format(year, season)] = df_gross_profit.apply (lambda row: ma2q_growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [13]:
# pandas styling
def color_white(val):
    """
    Takes a scalar and returns a string with
    the css property `'color: red'` for negative
    strings, black otherwise.
    """
    color = 'white'
    return 'color: %s' % color

def background_color(val):    
    if float(val) < 0:
        backgroundcolor = '#ff0000'
    elif float(val) < 10:
        backgroundcolor = '#f47721'
    elif float(val) < 20:
        backgroundcolor = '#ffdd00'
    elif float(val) < 30:
        backgroundcolor = '#5ecc62'
    else:
        backgroundcolor = '#00ad45'
    return 'background-color: %s' % backgroundcolor

In [14]:
def get_basic_info_for_ftock(stocktype):

    #get basic info of company
    '''
    抓取上市櫃股票的代號、名稱...等資料。
    上市
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=2
    上櫃
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=4
    '''
    #http://bloggerkaiweng.blogspot.com/2016/09/python.html

    if(stocktype == 'sii'):
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=2'
    else:
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=4'
    
    r = requests.get(url, stream=True, verify=False, proxies=proxyDict)
    r.encoding = 'big5hkscs' 
    dfshow = pd.read_html(r.text)

    for i, df in enumerate(dfshow):
        df.columns = df.iloc[0]
        dfshow[i] = df.iloc[1:]

    df = pd.concat(dfshow).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df['有價證券代號及名稱'] != '股票']
    df = df[~df['有價證券代號及名稱'].isnull()]
    df = df.reset_index(drop=True)
    
    newdf=df[df['產業別'] > '0']
    del newdf['國際證券辨識號碼(ISIN Code)'],newdf['CFICode'],newdf['備註']

    df2=newdf['有價證券代號及名稱'].str.split(' ', expand=True)
    df2 = df2.reset_index(drop=True)
    newdf = newdf.reset_index(drop=True)
    for i in df2.index:
        if '　' in df2.iat[i,0]:
            df2.iat[i,1]=df2.iat[i,0].split('　')[1]
            df2.iat[i,0]=df2.iat[i,0].split('　')[0]
    newdf=df2.join(newdf)
    newdf=newdf.rename(columns = {0:'公司代號',1:'股票名稱'})
    del newdf['有價證券代號及名稱']

    return newdf

In [15]:
df_basicinfo_sii = get_basic_info_for_ftock('sii').convert_objects(convert_numeric=True) #轉成float型態
df_basicinfo_otc = get_basic_info_for_ftock('otc').convert_objects(convert_numeric=True) #轉成float型態

df_basicinfo = pd.concat([df_basicinfo_sii,df_basicinfo_otc],axis=0, ignore_index=True)
#df_eps_basicinfo_sii.dtypes
#df_eps_basicinfo_otc

df_gross_profit = df_gross_profit.merge(df_basicinfo, on='公司代號', how='inner')

df_gross_profit

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  """Entry point for launching an IPython kernel.
C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:2: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  


公司代號     公司名稱  GrossProfit_107Q1  GrossProfit_106Q4  GrossProfit_106Q3  \
0     2801     彰化銀行                NaN                NaN                NaN   
1     2809     京城銀行                NaN                NaN                NaN   
2     2812     台中銀行                NaN                NaN                NaN   
3     2820       華票                NaN                NaN                NaN   
4     2834     臺灣企銀                NaN                NaN                NaN   
5     2836       高銀                NaN                NaN                NaN   
6     2838     聯邦銀行                NaN                NaN                NaN   
7     2845     遠東商銀                NaN                NaN                NaN   
8     2849     安泰銀行                NaN                NaN                NaN   
9     2855     統一證券                NaN                NaN                NaN   
10    2856     元富證券                NaN                NaN                NaN   
11    6005      群益證                NaN                NaN                NaN   
12    6024      群益期                NaN                NaN                NaN   
13    1101       台泥          5790640.0         18912914.0         12524003.0   
14    1102       亞泥          3329473.0         10171018.0          5961663.0   
15    1103       嘉泥            54830.0           282321.0           236084.0   
16    1104     環球水泥           138524.0           537908.0           423796.0   
17    1108     幸福水泥            20566.0           128501.0           205206.0   
18    1109     信大水泥           241008.0          1256014.0           722987.0   
19    1110       東泥            34457.0           -43205.0           -40823.0   
20    1201     味全公司          1104857.0          5553412.0          3978680.0   
21    1203     味王公司           488478.0          2020256.0          1499643.0   
22    1210     大成長城          2552191.0         10232733.0          7556152.0   
23    1213       大飲            16020.0            68492.0            62387.0   
24    1215     卜蜂企業           732606.0          3327986.0          2434799.0   
25    1216       統一         35429055.0        132740671.0        102775385.0   
26    1217      愛之味           325598.0          1304671.0          1074001.0   
27    1218     泰山企業           305219.0          1331364.0          1053629.0   
28    1219     福壽實業           268613.0           896460.0           635738.0   
29    1220       台榮            65957.0           274884.0           209987.0   
30    1225      福懋油           251047.0          1035870.0           790079.0   
31    1227       佳格          2289204.0          7399955.0          5484014.0   
32    1229     聯華實業           203445.0          1025092.0           777271.0   
33    1231     聯華食品           459088.0          1445489.0          1088640.0   
34    1232      大統益           429340.0          1685216.0          1249807.0   
35    1233       天仁           321597.0          1212380.0           912129.0   
36    1234       黑松           474380.0          2335035.0          1842255.0   
37    1235       興泰             -621.0             4798.0            17469.0   
38    1236     宏亞食品           161160.0           502744.0           303102.0   
39    1256  鮮活果汁-KY           221370.0           872790.0           734664.0   
40    1262    綠悅-KY            98650.0          1394442.0          1192669.0   
41    1301       台塑          9349215.0         33469176.0         25012107.0   
42    1303     南亞塑膠         13756954.0         49934342.0         36977513.0   
43    1304       台聚          1845606.0          7126932.0          5307297.0   
44    1305       華夏           970114.0          2776931.0          2025996.0   
45    1307     三芳化工           553730.0          2903725.0          2373599.0   
46    1308       亞聚            77798.0           697076.0           543453.0   
47    1309     台達化工           375252.0          1433704.0           949060.0   
48    1310       台苯           546139.0          1689216.0          1334821.0   
49    

In [16]:
# styled dataframe can use .to_excel('Styled_Basic_EPS.xlsx', engine='openpyxl') to export excel with style
year = 107
season = 1
howmany_year_data = 3

#first 4 quarter don't need to be calculated growth
columns_name = []
for i in range(int(howmany_year_data*4-4)):
    columns_name.append('Growth_{0}Q{1}'.format(year, season))
    columns_name.append('2QMAGrowth_{0}Q{1}'.format(year, season))
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

print(columns_name)
# the cell’s style depends only on it’s own value. That means we should use the Styler.applymap method which works elementwise.
# Now suppose you wanted to highlight the maximum value in each column. We can’t use .applymap anymore since that operated elementwise. Instead, we’ll turn to .apply which operates columnwise (or rowwise using the axis keyword).
#df_eps.style.applymap(color_negative_red, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).applymap(background_color, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).to_excel('Styled_Basic_EPS.xlsx', 'EPS_Basic', engine='openpyxl')
df_gross_profit.style.applymap(color_white, subset=pd.IndexSlice[:, columns_name]).applymap(background_color, subset=pd.IndexSlice[:, columns_name]).to_excel('Styled_Basic_Perspective_GrossProfit.xlsx', 'GrossProfit_Basic', engine='openpyxl')

# Pandas style function to hignlight specific columns
# http://pandas.pydata.org/pandas-docs/stable/style.html#Finer-Control:-Slicing
# Finer Control: Slicing
# ex: df.style.apply(highlight_max, subset=['B', 'C', 'D'])

['Growth_107Q1', '2QMAGrowth_107Q1', 'Growth_106Q4', '2QMAGrowth_106Q4', 'Growth_106Q3', '2QMAGrowth_106Q3', 'Growth_106Q2', '2QMAGrowth_106Q2', 'Growth_106Q1', '2QMAGrowth_106Q1', 'Growth_105Q4', '2QMAGrowth_105Q4', 'Growth_105Q3', '2QMAGrowth_105Q3', 'Growth_105Q2', '2QMAGrowth_105Q2']


C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\pandas\core\indexing.py:1472: FutureWarning: 
Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate-loc-reindex-listlike
  return self._getitem_tuple(key)
